# Replicating fig 2 graphs with the curves of the RL model with different richness and the foraging model for different thresholds

In [1]:
import random
import numpy as np
import pandas as pd
from scipy import interpolate


In [4]:
max_steps = 300

n_humans = 400
p_red_human = np.empty((max_steps,n_humans))
p_blue_human = np.empty((max_steps,n_humans))
humans_perceived_value = np.empty((max_steps,n_humans))
humans_choices = np.empty((max_steps,n_humans))
humans_explore_or_exploit = np.empty((max_steps,n_humans))

chosen_options_foraging = np.empty((max_steps))
chosen_options_foraging[:] = np.nan
rewards_foraging = np.empty((max_steps))
rewards_foraging[:] = np.nan

explore_or_exploit = np.zeros((max_steps))
termination_probabilities = np.zeros((max_steps))
q_table_foraging = np.zeros((max_steps))
q_table_foraging[0] = 0.4

def get_p_exploit(last_value, beta, threshold):
    return 1/(1+np.exp(-beta*(last_value-threshold)))

def explore(options, last_value, threshold, beta, alpha, time, human, rng):
    chosen_option = rng.choice(options)
    probability = p_red_human[time,human] if chosen_option == 0 else p_blue_human[time,human]
    termination_probability = get_p_exploit(last_value, beta, threshold)
    reward = get_reward(probability, rng)
    last_value = last_value + alpha * (reward - last_value)
    return termination_probability, chosen_option, last_value, reward

def exploit(last_option, last_value, threshold, beta, alpha, time, human, rng):
    probability = p_red_human[time,human] if last_option == 0 else p_blue_human[time,human]
    termination_probability = 1 - get_p_exploit(last_value, beta, threshold)
    reward = get_reward(probability, rng)
    last_value = last_value + alpha * (reward - last_value)
    return termination_probability, last_value, reward

In [2]:
def get_reward(probability, rng):
    if rng.uniform(0,1) < probability:
        return 1
    else:
        return 0


In [16]:
beta_foraging = 3
alpha_foraging = 0.3
rng_foraging = np.random.default_rng()
state = "explore"
threshold = 0.4
last_value = q_table_foraging[0]
options = [0,1] #red, blue
hazard_rate = 0.1
p_red_human[0,:] = 0.5
p_blue_human[0,:] = 0.5
for human in range(n_humans):
    for step in range(max_steps):
        if step+1 < max_steps:
            delta_p = rng_foraging.choice([-0.1,0.1]) if rng_foraging.uniform(0,1) < hazard_rate else 0
            p_red_human[step+1,human] = max(min(p_red_human[step,human]+delta_p,1.0),0)
            delta_p = rng_foraging.choice([-0.1,0.1]) if rng_foraging.uniform(0,1) < hazard_rate else 0
            p_blue_human[step+1,human] = max(min(p_blue_human[step,human]+delta_p,1.0),0)
        match state:
            case "explore":
                termination_probability, last_option, last_value, reward = explore(options, last_value, threshold, beta_foraging, alpha_foraging, step, human, rng_foraging)
                chosen_options_foraging[step] = last_option
                termination_probabilities[step] = termination_probability
                rewards_foraging[step] = reward 
                explore_or_exploit[step] = 0
                if step+1 < max_steps:
                        q_table_foraging[step+1] = last_value
                if (rng_foraging.uniform(0,1) < termination_probability):
                    state = "exploit"
            case "exploit":
                termination_probability, last_value, reward = exploit(last_option, last_value, threshold, beta_foraging, alpha_foraging, step, human, rng_foraging)
                chosen_options_foraging[step] = last_option
                rewards_foraging[step] = reward
                termination_probabilities[step] = termination_probability
                explore_or_exploit[step] = 1
                if step+1 < max_steps:
                        q_table_foraging[step+1] = last_value
                if (rng_foraging.uniform(0,1) < termination_probability):
                    state = "explore"
    humans_perceived_value[:,human] = q_table_foraging
    humans_choices[:,human] = chosen_options_foraging
    humans_explore_or_exploit[:,human] = explore_or_exploit


In [17]:
human = 1
fig_after = create_fig_of_RL_foraging_experiment(humans_choices[:,human], humans_perceived_value[:,human], p_red_human[:,human], p_blue_human[:,human], threshold, humans_explore_or_exploit[:,human])
fig_after.show()

In [14]:
import plotly.graph_objects as go
def create_fig_of_RL_foraging_experiment(chosen_options, q_table, p_red, p_blue, threshold, explore_or_exploit, termination_probabilities=[]):
    fig = go.Figure()

    #add original probabilities
    x = np.linspace(1,300,300)
    y = p_red
    y2 = p_blue
    fig.add_trace(go.Scatter(x=x,y=y, name="Option 1 Ideal", mode='lines', opacity=0.5, line={"color":"#C37364"}))
    fig.add_trace(go.Scatter(x=x,y=y2, name="Option 2 Ideal", mode='lines', opacity=0.5, line={"color":"#136EAC"}))

    #add foraging  RL model
    # fig.add_trace(go.Scatter(x=x,y=termination_probabilities[:], name="Chosen Option Value", mode='lines', opacity=1, line={"color":"#FF0CE7"}))
    fig.add_trace(go.Scatter(x=x,y=q_table[:], name="Chosen Option Value", mode='lines', opacity=1, line={"color":"#9D516F"}))
    

    # Add reward outcome points at the top
    chosen_options_y_red = np.ones(len(chosen_options)) * 1.075  # Slightly above 1
    chosen_options_y_blue = np.ones(len(chosen_options)) * 1.050  # Slightly above 1
    chosen_options_y_explore = np.ones(len(chosen_options)) * 1.175  # Slightly above 1
    chosen_options_y_exploit = np.ones(len(chosen_options)) * 1.150  # Slightly above 1
    # chosen_options_x = np.arange(1, len(chosen_options) + 1)

    #add threshold
    fig.add_trace(go.Scatter(x=x,y=np.ones(len(chosen_options)) * threshold, name="Chosen Option Value", mode='lines', opacity=1, line={"color":"#399563"}))
    
    # Red dots (reward = 0)
    fig.add_trace(go.Scatter(
        x=x[chosen_options == 0],
        y=chosen_options_y_red[chosen_options == 0],
        mode='markers',
        marker=dict(color='#C37364', size=6),
        name='Chosen option: Red'
    ))

    # Blue dots (reward = 1)
    fig.add_trace(go.Scatter(
        x=x[chosen_options == 1],
        y=chosen_options_y_blue[chosen_options == 1],
        mode='markers',
        marker=dict(color='#136EAC', size=6),
        name='Chosen option: Blue'
    ))
    
    # Explore dots (reward = 0)
    fig.add_trace(go.Scatter(
        x=x[explore_or_exploit == 0],
        y=chosen_options_y_explore[explore_or_exploit == 0],
        mode='markers',
        marker=dict(color="#0DAE25", size=6),
        name='Explore'
    ))

    # Exploit dots (reward = 1)
    fig.add_trace(go.Scatter(
        x=x[explore_or_exploit == 1],
        y=chosen_options_y_exploit[explore_or_exploit == 1],
        mode='markers',
        marker=dict(color="#9E0CA3", size=6),
        name='Exploit'
    ))

    fig.update_layout(yaxis=dict(range=[0, 1.25]))  # Adjust y-axis to fit dots
    return fig

# Now, let's try to recreate the graph:

In [22]:
def get_discriminability_2(a: list,b: list):
    # return abs(a-b)
    return np.divide(abs(a-b),(a+b), out=np.zeros_like(a), where=(a+b)!=0)

In [23]:
humans_discriminability_100_trials2 = np.empty((max_steps,n_humans))
humans_richness_100_trials2 = np.empty((max_steps,n_humans))
humans_delta_reward = np.empty((max_steps,n_humans))
x = np.linspace(1,300,300)
for human in range(n_humans):
    humans_discriminability_100_trials2[:,human] = get_discriminability_2(p_red_human[:,human], p_blue_human[:,human])
    humans_richness_100_trials2[:,human] = (p_red_human[:,human] + p_blue_human[:,human])
    humans_delta_reward[:,human] = abs(p_red_human[:,human] - p_blue_human[:,human])

In [24]:
fig_richness_discriminability2 = go.Figure()
fig_richness_discriminability2.add_trace(go.Scatter(x=humans_richness_100_trials2[:,1],y=humans_discriminability_100_trials2[:,0],
                                                   name="A", mode='markers', opacity=1, line={"color":"#C3BD64"}))
fig_richness_discriminability2.show()

In [25]:
switch_per_human = np.empty((max_steps,n_humans,4))
for human in range(n_humans):
    switch_per_human[:,human,0] = humans_richness_100_trials2[:,human] < 0.9
    switch_per_human[:,human,1] = humans_richness_100_trials2[:,human] < 0.7
    switch_per_human[:,human,2] = humans_richness_100_trials2[:,human] < 0.5
    switch_per_human[:,human,3] = humans_richness_100_trials2[:,human] < 0.3

In [26]:
print(sum(switch_per_human[:,1,0]),
sum(switch_per_human[:,1,1]),
sum(switch_per_human[:,1,2]),
sum(switch_per_human[:,1,3]))

276.0 96.0 54.0 9.0


In [62]:
human = 0
fig_after = create_fig_of_RL_foraging_experiment_with_richness(humans_choices[:,human], humans_perceived_value[:,human], p_red, p_blue, threshold, humans_explore_or_exploit[:,human], humans_richness_100_trials2[:,human])
fig_after.show()

In [27]:
hist = go.Figure()
hist.add_histogram(x=humans_discriminability_100_trials2[:,1], y=switch_per_human[:,1,3], nbinsx=10, histfunc='avg')
hist.show()
hist2 = go.Figure()
hist2.add_histogram(x=humans_richness_100_trials2[:,1], y=switch_per_human[:,1,3], nbinsx=10, histfunc='avg')
hist2.show()

In [70]:

# Bin discriminability for plotting average p(switch)
bins = np.linspace(0, 1.049, 11)
bin_centers = 0.5 * (bins[:-1] + bins[1:])
binned_switch = []

thresholds = [0.9, 0.7, 0.5, 0.3]  # Thresholds for switching
human = 1
for i, t in enumerate(thresholds):
    digitized = np.digitize(humans_discriminability_100_trials2[:,human], bins)
    bin_means = [switch_per_human[digitized == j,human,i].mean() if np.any(digitized == j) else np.nan for j in range(1, len(bins))]
    binned_switch.append(bin_means)
fig = go.Figure()

colors = ['goldenrod', 'darkorange', 'lightseagreen', 'teal']
for i, t in enumerate(thresholds):
    fig.add_trace(go.Scatter(
        x=bin_centers,
        y=binned_switch[i],
        mode='lines+markers',
        name=f'Δ reward < {t}',
        line=dict(color=colors[i]),
        marker=dict(size=6)
    ))

fig.update_layout(
    title='Compare-Alternatives Model: p(switch) vs Discriminability',
    xaxis_title='Discriminability',
    yaxis_title='p(switch)',
    legend_title='Thresholds',
    template='plotly_white'
)

fig.show()

In [69]:

# Bin richness for plotting average p(switch)
bins = np.linspace(0, 2, 11)
bin_centers = 0.5 * (bins[:-1] + bins[1:])
binned_switch = []

thresholds = [0.9, 0.7, 0.5, 0.3]  # Thresholds for switching
human = 1
for i, t in enumerate(thresholds):
    digitized = np.digitize(humans_richness_100_trials2[:,human], bins)
    bin_means = [switch_per_human[digitized == j,human,i].mean() if np.any(digitized == j) else np.nan for j in range(1, len(bins))]
    binned_switch.append(bin_means)
fig = go.Figure()

colors = ['goldenrod', 'darkorange', 'lightseagreen', 'teal']
for i, t in enumerate(thresholds):
    fig.add_trace(go.Scatter(
        x=bin_centers,
        y=binned_switch[i],
        mode='lines+markers',
        name=f'Δ reward < {t}',
        line=dict(color=colors[i]),
        marker=dict(size=6)
    ))

fig.update_layout(
    title='Compare-Alternatives Model: p(switch) vs richness',
    xaxis_title='richness',
    yaxis_title='p(switch)',
    legend_title='Thresholds',
    template='plotly_white'
)

fig.show()

# Now trying with all the values

In [35]:
# Bin discriminability for plotting average p(switch)
bins = np.linspace(0, 2, 11)
bin_centers = 0.5 * (bins[:-1] + bins[1:])
binned_switch = []

thresholds = [0.9, 0.7, 0.5, 0.3]  # Thresholds for switching
human = 1
for i, t in enumerate(thresholds):
    digitized = np.digitize(humans_discriminability_100_trials2[:,:], bins)
    bin_means = [switch_per_human[digitized == j,i].mean() if np.any(digitized == j) else np.nan for j in range(1, len(bins))]
    print(bin_means)
    binned_switch.append(bin_means)
fig = go.Figure()

colors = ['goldenrod', 'darkorange', 'lightseagreen', 'teal']
for i, t in enumerate(thresholds):
    fig.add_trace(go.Scatter(
        x=bin_centers,
        y=binned_switch[i],
        mode='lines+markers',
        name=f'Δ reward < {t}',
        line=dict(color=colors[i]),
        marker=dict(size=6)
    ))

fig.update_layout(
    title='Compare-Alternatives Model: p(switch) vs Discriminability',
    xaxis_title='Discriminability',
    yaxis_title='p(switch)',
    legend_title='Thresholds',
    template='plotly_white'
)

fig.show()

[0.18914632890536506, 0.28359288733198795, 0.42640322313593465, 0.6325884543761638, 0.29244323957980345, 0.8770565360454682, nan, nan, nan, nan]
[0.09352280918545978, 0.15535163538057342, 0.17638942546498151, 0.24515828677839852, 0.2893934259573026, 0.602078970984146, nan, nan, nan, nan]
[0.04063433220059726, 0.05646727335034078, 0.10160604889894585, 0.0, 0.2893934259573026, 0.37481304217768474, nan, nan, nan, nan]
[0.019050561219235918, 0.0, 0.0, 0.0, 0.2893934259573026, 0.13969488483398146, nan, nan, nan, nan]


In [36]:

# Bin richness for plotting average p(switch)
bins = np.linspace(0, 2, 11)
bin_centers = 0.5 * (bins[:-1] + bins[1:])
binned_switch = []

thresholds = [0.9, 0.7, 0.5, 0.3] # Thresholds for switching
human = 1
for i, t in enumerate(thresholds):
    digitized = np.digitize(humans_richness_100_trials2[:,:], bins)
    bin_means = [switch_per_human[digitized == j,i].mean() if np.any(digitized == j) else np.nan for j in range(1, len(bins))]
    binned_switch.append(bin_means)
fig = go.Figure()

colors = ['goldenrod', 'darkorange', 'lightseagreen', 'teal']
for i, t in enumerate(thresholds):
    fig.add_trace(go.Scatter(
        x=bin_centers,
        y=binned_switch[i],
        mode='lines+markers',
        name=f'Δ reward < {t}',
        line=dict(color=colors[i]),
        marker=dict(size=6)
    ))

fig.update_layout(
    title='Compare-Alternatives Model: p(switch) vs richness',
    xaxis_title='richness',
    yaxis_title='p(switch)',
    legend_title='Thresholds',
    template='plotly_white'
)

fig.show()

In [ ]:
print(switch_per_human.shape)
print(switch_per_human.reshape(-1,4).shape)
print(np.array_equal( switch_per_human.reshape(-1,4)[:,0].reshape(300,400), switch_per_human[:,:,0]))

(300, 400, 4)
(120000, 4)
True


In [41]:
hist = go.Figure()
hist.add_histogram(x=humans_discriminability_100_trials2.flatten(), y=switch_per_human.reshape(-1,4)[:,3], nbinsx=10, histfunc='avg')
hist.show()

bins = np.linspace(0, 2, 11)
hist2 = go.Figure()
hist2.add_histogram(x=humans_richness_100_trials2.flatten(), y=switch_per_human.reshape(-1,4)[:,3], xbins=dict(start=0,end=2,size=0.2), histfunc='avg')
hist2.show()

In [148]:
a = np.arange(0,27).reshape(3,3,3) - 10
a<0


array([[[ True,  True,  True],
        [ True,  True,  True],
        [ True,  True,  True]],

       [[ True, False, False],
        [False, False, False],
        [False, False, False]],

       [[False, False, False],
        [False, False, False],
        [False, False, False]]])

In [117]:
my_discriminability = np.divide(abs(humans_perceived_values[0,:,:] - humans_perceived_values[1,:,:]), (humans_perceived_values[0,:,:] + humans_perceived_values[1,:,:]))

In [116]:
np.divide([1,2,3],[4,5,6])

array([0.25, 0.4 , 0.5 ])

In [118]:
fig_p_switch_discriminability2 = go.Figure()
for human in range(30):
    fig_p_switch_discriminability2.add_trace(go.Scatter(x=humans_richness_100_trials2[:,human],y=my_discriminability[:,human],
                                                   name="A", mode='markers', opacity=1, line={"color":"#C3BD64"}))
fig_p_switch_discriminability2.show()

In [114]:
p_switch_per_human = np.empty((max_steps,n_humans,4))
for human in range(n_humans):
    p_switch_per_human[:,human,0] = sum(my_discriminability[:,human] < 0.05)/len(my_discriminability[:,human])
    p_switch_per_human[:,human,1] = sum(my_discriminability[:,human] < 0.1)/len(my_discriminability[:,human])
    p_switch_per_human[:,human,2] = sum(my_discriminability[:,human] < 0.2)/len(my_discriminability[:,human])
    p_switch_per_human[:,human,3] = sum(my_discriminability[:,human] < 0.4)/len(my_discriminability[:,human])

In [ ]:
fig_p_switch = go.Figure()
for p in range(4):
    for human in range(1):
        fig_p_switch_discriminability2.add_trace(go.Scatter(x=humans_richness_100_trials2[:,human],y=p_switch_per_human[:,human,p],
                                                   name="A", mode='markers', opacity=1, line={"color":"#C3BD64"}))
fig_p_switch_discriminability2.show()

In [47]:

delta_reward_probability1 = q_table[0,:100]-q_table[1,:100]
delta_reward_probability2 = q_table[0,:200]-q_table[1,:200]
delta_reward_probability3 = q_table[0,:300]-q_table[1,:300]
discriminability1 = get_discriminability(numbers1)
discriminability2 = get_discriminability(numbers1)
discriminability3 = get_discriminability(numbers1)
richness1 = np.sum(q_table[0,:100]+q_table[1,:100])
richness2 = np.sum(q_table[0,:200]+q_table[1,:200])
richness3 = np.sum(q_table[0,:300]+q_table[1,:300])

In [29]:
get_discriminability(q_table[1,:100])

0.016267211474063712

In [33]:
l = [0, 1, 1]
display(get_discriminability(l))

0.5

2

In [ ]:
import plotly.graph_objects as go
def create_fig_of_RL_foraging_experiment_with_richness(chosen_options, q_table, p_red, p_blue, threshold, explore_or_exploit, richness, termination_probabilities=[]):
    fig = go.Figure()

    #add original probabilities
    x = np.linspace(1,300,300)
    y = p_red
    y2 = p_blue
    fig.add_trace(go.Scatter(x=x,y=y, name="Option 1 Ideal", mode='lines', opacity=0.5, line={"color":"#C37364"}))
    fig.add_trace(go.Scatter(x=x,y=y2, name="Option 2 Ideal", mode='lines', opacity=0.5, line={"color":"#136EAC"}))

    #add foraging  RL model
    # fig.add_trace(go.Scatter(x=x,y=termination_probabilities[:], name="Chosen Option Value", mode='lines', opacity=1, line={"color":"#FF0CE7"}))
    fig.add_trace(go.Scatter(x=x,y=q_table[:], name="Chosen Option Value", mode='lines', opacity=1, line={"color":"#9D516F"}))
    
    fig.add_trace(go.Scatter(x=x,y=richness, name="Richness", mode='lines', opacity=1, line={"color":"#C9A71F"}))

    # Add reward outcome points at the top
    chosen_options_y_red = np.ones(len(chosen_options)) * 1.075  # Slightly above 1
    chosen_options_y_blue = np.ones(len(chosen_options)) * 1.050  # Slightly above 1
    chosen_options_y_explore = np.ones(len(chosen_options)) * 1.175  # Slightly above 1
    chosen_options_y_exploit = np.ones(len(chosen_options)) * 1.150  # Slightly above 1
    # chosen_options_x = np.arange(1, len(chosen_options) + 1)

    #add threshold
    fig.add_trace(go.Scatter(x=x,y=np.ones(len(chosen_options)) * threshold, name="Chosen Option Value", mode='lines', opacity=1, line={"color":"#399563"}))
    
    # Red dots (reward = 0)
    fig.add_trace(go.Scatter(
        x=x[chosen_options == 0],
        y=chosen_options_y_red[chosen_options == 0],
        mode='markers',
        marker=dict(color='#C37364', size=6),
        name='Chosen option: Red'
    ))

    # Blue dots (reward = 1)
    fig.add_trace(go.Scatter(
        x=x[chosen_options == 1],
        y=chosen_options_y_blue[chosen_options == 1],
        mode='markers',
        marker=dict(color='#136EAC', size=6),
        name='Chosen option: Blue'
    ))
    
    # Explore dots (reward = 0)
    fig.add_trace(go.Scatter(
        x=x[explore_or_exploit == 0],
        y=chosen_options_y_explore[explore_or_exploit == 0],
        mode='markers',
        marker=dict(color="#0DAE25", size=6),
        name='Explore'
    ))

    # Exploit dots (reward = 1)
    fig.add_trace(go.Scatter(
        x=x[explore_or_exploit == 1],
        y=chosen_options_y_exploit[explore_or_exploit == 1],
        mode='markers',
        marker=dict(color="#9E0CA3", size=6),
        name='Exploit'
    ))

    fig.update_layout(yaxis=dict(range=[0, 1.25]))  # Adjust y-axis to fit dots
    return fig